Required imports:

In [4]:
import numpy as np
import random
import numpy.polynomial.polynomial as polynom
import numpy.linalg as linalg
from scipy import sparse
from scipy.sparse.linalg import spsolve
import matplotlib.pyplot as plt

Main class: Mesh ...

In [10]:
class Mesh:
    def __init__(self, omega,number_media,length_media,rho_media,mu_media,h_glob,order_glob):
        #omega : frequency
        #number_media : number of layers
        #length_media : a vector of size number_media containing the length of each layer
        #rho_media : a vector of size number_media containing the density of each layer
        #mu_media : a vector of size number_media containing the bulk modulus of each layer
        length=0         #the total length
        rho=[]            #a vector containing the density of each cell of the mesh        
        mu=[]        #a vector containing the bulk modulus of each cell of the mesh        
        order=[]  #a vector containing the polynomial order of each cell of the mesh        
        nbpoints=1; # the number of nodes of the mesh
        nbele=0; # the number of elements of the mesh
        coor=[0]        #a vector of size nbpoints, containing the coordinates of each node of the mesh
        ele=[]          # a table of size nbele x 2 : the first columns gives the first node of the celle, the second gives the second nodes. It is useless in 1D, but we set it in order to mimic 2D and 3D
        L=0;
        for i in range(0,number_media) :
            #we loop over all the layers
            L=L+length_media[i]     #we increase the total length by the size of the current layer
            c=np.sqrt(mu_media[i]/rho_media[i]) #we compute the speed of the acoustic wave
            h=h_glob #the size of the cells in the layer
            order_cell=order_glob #the order of the cells in the layer
            wavelength=c*2*np.pi/omega
            if order_cell == 1:
                h=wavelength/100
            elif order_cell == 2:
                h=wavelength/20
            elif order_cell == 3:
                h=wavelength/6
            elif order_cell == 4:
                h=wavelength/4
            elif order_cell == 5:
                h=wavelength/3
            elif order_cell > 6:
                h=wavelength/2
            N=int(np.floor(length_media[i]/h)) #we compute the number of cells of the layer
            for j in range (0,N-1):
                #we construct the cells of the layer i
                nbele=nbele+1 #we increase the number  of cells
                nbpoints=nbpoints+1 #we increase the number  of nodes
                length=length+h #we increase the length by h
                coor.append(length) #this is the coordinate of the new node
                rho.append(rho_media[i]) #the density of the cell is rho_media[i]
                mu.append(mu_media[i]) #the bulk modulus of the cell is mu_media[i]
                order.append(order_cell) #the bulk modulus of the cell is order_global
                ele.append(nbpoints-2) #the two nodes of the elements are nbpoints-2 and nbpoints-1
                ele.append(nbpoints-1)
            #now, we define the last cell of the layer
            nbele=nbele+1
            nbpoints=nbpoints+1
            length=L;
            coor.append(length)
            rho.append(rho_media[i])
            mu.append(mu_media[i])
            order.append(order_cell)
            ele.append(nbpoints-2)
            ele.append(nbpoints-1)

        self.ele=np.reshape(np.array(ele),[nbele,2])
        self.coor=np.array(coor)
        self.rho=np.array(rho)
        self.mu=np.array(mu)
        self.nbele=nbele
        self.nbpoints=nbpoints
        self.order=order

Basis functions [...] Fill [...]

In [6]:
class Basis:
    def __init__(self, p):
        #p is the order of the basis
        #we build the p+1 elementary polynomials of degree 1
        poly_elem=np.zeros((p+1,2)) #poly_elem is table (p+1)x2 : each line contains the coefficients a and b such that the polynom reads as a+bx. 
        for i in range(0,p+1):
            #the root of polynonimal i is i/p, so that a=-i/p and b=1;
            poly_elem[i,0]=-(i)/p
            poly_elem[i,1]=1
            #we initialize the basis
            phi=[]
            #phi is a vector of vector : phi[i] is the basis function i which is a polynomial of degree p, it represented by a vector of size p+1 containing the coefficients of the polynomial fom the lowest to the highest
        for i in range(0,p+1):
            #the basis function i is the product of all elementary polynomials except polynomial i. It is normalized so that phi[i](i)=1
            #we start with the constant polynomial
            phi.append([1])
            for j in range(0,p+1):
                if i!=j:
                    phi[i]=polynom.polymul(phi[i],poly_elem[j,:])
                    #we multiply phi[i] by all elementary polynomials except polynomial i
            phi[i]=phi[i]/polynom.polyval(i/p,phi[i])
            #we normalize phi[i]
        self.phi=phi
        massmat=np.zeros((p+1,p+1))#we initialize the mass matrix
        stiffmat=np.zeros((p+1,p+1))#we initialize the stiffness matrix
        for i in range(0,p+1):
            for j in range(0,p+1):
                massmat[i,j]=sum(polynom.polyint(polynom.polymul(phi[i],phi[j])))
                stiffmat[i,j]=sum(polynom.polyint(polynom.polymul(phi[i],polynom.polyder(phi[j]))))
        self.massmat=massmat
        self.stiffmat=stiffmat


Class for local matrices and rhs ...

In [7]:
#This class contains the local matrix and rhs        
class Elem:
    def __init__(self, x0,x1,rho,mu,order,alpha,basis,omega,xs):
        #x0 : left coordinate of the cell
        #x1 :  right coordinate of the cell
        #rho : density of the cell
        #mu : bulk modulus of the cell
        #order : order of the cell
        #alpha : penalization coefficient
        #basis : the basis functions
        #omega : the frequency
        #xs : the position of the source, if any
        n=order+1; #the number of degree of freedom in the cell
        h=x1-x0 #the length of the cell
        mat=np.zeros((2*n,2*n),dtype=complex) #initialization of the matrix
        rhs=np.zeros((2*n),dtype=complex) #initialization of the rhs

        #the four blocks of the matrix
        mat[:n,:n]=1j*omega*h/mu*basis.massmat
        mat[n:,:n]=-basis.stiffmat
        mat[:n,n:]=basis.stiffmat.T
        mat[n:,n:]=1j*omega*h*rho*basis.massmat
 
#we add the penalization coefficients
        mat[n,n]=mat[n,n]-alpha;
        mat[2*n-1,2*n-1]=mat[2*n-1,2*n-1]-alpha;

        F=np.zeros((2*n,2)) #the right hand side
        F[0,0]=-1
        F[n-1,1]=1
        F[n,0]=-alpha
        F[2*n-1,1]=-alpha

        
        #computation of the source if it is inside the element
        if (xs>=x0 and xs<=x1):
        #we compute the coordinates of the source in the reference element
            xs_ref=(xs-x0)/h
            for i in range(n):
                #we compute the values of basis functions at point xs_ref
                 rhs[i]=polynom.polyval(xs_ref,basis.phi[i])
            #the source is only on the pressure
            rhs[n:]=0
            rhs=linalg.solve(mat,rhs)
        else:
            rhs[:]=0

            
        self.mat=linalg.solve(mat,F)
        self.rhs=rhs

Sparse management

In [8]:
class Sparse:
    def __init__(self,alpha,elem,nbpoints,order):
        #alpha : penalization coefficient
        #elem : the local matrices associated to each elements
        #nbpoints : the number of vertices of the mesh
        #order : a vector containing the order of each element
        
        #the global matrices is stored in coordinate format : 
        A=[]; #the vector containing the non-zero values
        I=[]; # the vector containing the lines of the non-zero values
        J=[];# the vector containing the columns of the non-zero values
        #we have Mat(I[i], J[i])=A[i]
        B=[];# the Right Hand Side
        

        #Left point of the mesh
        p=order[0]
        
        res=elem[0].mat[0,0]-2*alpha*elem[0].mat[p+1,0]+2*alpha
        A.append(res)
        I.append(0)
        J.append(0)
        
        res=elem[0].mat[0,1]-2*alpha*elem[0].mat[p+1,1];
        A.append(res)
        I.append(1)
        J.append(0)

        #right hand side
        res=-elem[0].rhs[p]+2*alpha*(elem[0].rhs[2*p+1]);
        B.append(res)

        #now we run on all the vertices of the mesh (except the left and right ones)
        for i in range(1,nbpoints-1):
            #we get the order of elem i-1 and i
            p1=order[i-1]
            p2=order[i]
            
            res=-elem[i-1].mat[p1,0]-alpha*elem[i-1].mat[2*p1+1,0]
            A.append(res)
            I.append(i-1)
            J.append(i)
            
            res=-elem[i-1].mat[p1,1]-alpha*elem[i-1].mat[2*p1+1,1]+elem[i].mat[0,0]-alpha*elem[i].mat[p2+1,0]+2*alpha
            A.append(res)
            I.append(i)
            J.append(i)
            
            res=elem[i].mat[0,1]-alpha*elem[i].mat[p2+1,1]
            A.append(res)
            I.append(i+1)
            J.append(i)

            #right hand side
            res=-(elem[i].rhs[p2]-elem[i-1].rhs[0])+alpha*(elem[i].rhs[2*p2+1]+elem[i-1].rhs[p1+1])
            B.append(res)

        #right point of the mesh            
        p=order[nbpoints-2]        
        res=-elem[nbpoints-2].mat[p,0]-2*alpha*elem[nbpoints-2].mat[2*p+1,0]
        A.append(res)
        I.append(nbpoints-2)
        J.append(nbpoints-1)
        res=-elem[nbpoints-2].mat[p,1]-2*alpha*elem[nbpoints-2].mat[2*p+1,1]+2*alpha;           
        A.append(res)
        I.append(nbpoints-1)
        J.append(nbpoints-1)
        
        res=elem[nbpoints-2].rhs[0]+2*alpha*elem[nbpoints-2].rhs[p+1]
        B.append(res)

        # Left and right boundary condition. Comment only if there is a point soucre
        B[0]=0;
        B[nbpoints-1]=-np.sin(omega*mesh.coor[nbpoints-1]);
        self.matrix = sparse.coo_matrix((A,(I,J)),shape=(nbpoints,nbpoints))
        self.rhs = B

In [14]:
alpha=.5 #penalization parameter
omega=10 #frequency
x_source=20 #position of the source (if no source, put it outside of the domain)
nb_media=1 #number of layer
points_plot=10 #number of points on each cell for plotting the solution
h_glob=0.05 #Global size of the cells
order_glob=2 #Global order of the cells
length_media=[1] #Length of the layers
rho_media=[1] #density of the layers
mu_media=[1] #bulk modulus of the layers
mesh = Mesh(omega,nb_media,length_media,rho_media,mu_media,h_glob,order_glob)#we create the mesh
basis=list(range(max(mesh.order)+1)) 
for p in set(mesh.order):
    print ("building basis functions of order", p)
    basis[p]=Basis(p)#we define all the basis functions we need

elem=list(range(mesh.nbele+1))
for i in range(mesh.nbele):
    #we run over all the cells of the mesh
    node=mesh.ele[i]
    x0=mesh.coor[node[0]]
    x1=mesh.coor[node[1]]
    rho=mesh.rho[i]
    mu=mesh.mu[i]
    order=mesh.order[i]
    elem[i]=Elem(x0,x1,rho,mu,order,alpha,basis[order],omega,x_source) #we construct the elementary basis functions

linsys=Sparse(alpha,elem,mesh.nbpoints,mesh.order) # we create the global linear system
Lambda=spsolve(linsys.matrix,linsys.rhs)#we solve the linear system
#plt.plot(np.imag(Lambda))
#plt.show()
#Computation of the solution

#Now, we reconstruct the solution on each element of the mesh
P=[]
U=[]
X=[]
P_ex=[]
U_ex=[]
err_U=0
err_P=0
L2_U=0
L2_P=0
#we run over all the elements of the mesh
for i in range(mesh.nbele):
    #we find the two vertices of the element
    node=mesh.ele[i,:]
    #we get the two lambda associated to these vertices    
    lambda_loc=Lambda[node]
    #we can now compute locally the solution on the element
    W_K= np.dot(elem[i].mat,lambda_loc)+elem[i].rhs
    #the first degrees of freedom are associated to the pressure
    p=mesh.order[i]
    P_K=W_K[:p+1];
    #the last degrees of freedom are associated to the velocity
    U_K=W_K[p+1:];
    #we compute the value of P and U on the points of the submesh
    for j in range(points_plot+1):
        x=j/points_plot
        xcoor=mesh.coor[node[0]]+x*(mesh.coor[node[1]]-mesh.coor[node[0]])
        X.append(xcoor)
        P_exact=np.sin(omega*xcoor)
        U_exact=-1j*np.cos(omega*xcoor)
        P_ex.append(P_exact)
        U_ex.append(U_exact)
        valP=0
        valU=0
        #We get the order of the cell
        for k in range(p+1):
            val=polynom.polyval(x,basis[p].phi[k])
            valP=valP+val*P_K[k]
            valU=valU+val*U_K[k]
        P.append(valP)
        U.append(valU)
        err_P=err_P+abs(valP-P_exact)*abs(valP-P_exact)
        err_U=err_U+abs(valU-U_exact)*abs(valU-U_exact)
        L2_P=L2_P+abs(P_exact)*abs(P_exact)
        L2_U=L2_U+abs(U_exact)*abs(U_exact)
#computation of relative  L2 error
c=np.sqrt(mu/rho)
print('number of point per waverlength', c*2*np.pi/omega/h_glob)
print("relative L2 error on P :", np.sqrt(err_P/L2_P) )
print("relative L2 error on U :", np.sqrt(err_U/L2_U) )
    

building basis functions of order 2
number of point per waverlength 12.566370614359172
relative L2 error on P : 0.0028033575723539024
relative L2 error on U : 0.00283144191252979
